In [1]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D
from tensorflow.keras.applications import ResNet50
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint, ReduceLROnPlateau
import tensorflow as tf
print("Import erfolgreich")


Import erfolgreich


In [2]:
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from sklearn.model_selection import train_test_split
import os

base_dir = 'pokemon'

image_size = (224, 224)
batch_size = 32

train_datagen = ImageDataGenerator(
    rescale=1./255,
    rotation_range=40,
    width_shift_range=0.2,
    height_shift_range=0.2,
    shear_range=0.2,
    zoom_range=0.2,
    horizontal_flip=True,
    fill_mode='nearest',
    validation_split=0.2  
)

train_generator = train_datagen.flow_from_directory(
    base_dir,
    target_size=image_size,
    batch_size=batch_size,
    class_mode='categorical',
    subset='training' 
)

validation_generator = train_datagen.flow_from_directory(
    base_dir,
    target_size=image_size,
    batch_size=batch_size,
    class_mode='categorical',
    subset='validation' 
)

# Aktuellen Arbeitspfad drucken
print("Aktueller Arbeitspfad:", os.getcwd())

# Inhalte im aktuellen Verzeichnis auflisten
print("Verzeichnisinhalt:", os.listdir())

Found 361 images belonging to 3 classes.
Found 89 images belonging to 3 classes.
Aktueller Arbeitspfad: c:\Users\lukas\Studium\6. Semester\KI Anwendungen\PIcture
Verzeichnisinhalt: ['.history', '.ipynb_checkpoints', 'app.py', 'main.ipynb', 'pokemon']


In [3]:
base_model = ResNet50(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

base_model.trainable = False

model = Sequential([
    base_model,
    GlobalAveragePooling2D(),
    Dense(512, activation='relu'),
    Dense(3, activation='softmax')  
])

model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

early_stopping = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)
model_checkpoint = ModelCheckpoint('best_model.keras', save_best_only=True)
reduce_lr = ReduceLROnPlateau(monitor='val_loss', factor=0.2, patience=2, min_lr=1e-7)


In [4]:
history = model.fit(
    train_generator,
    epochs=10,
    validation_data=validation_generator,
    callbacks=[early_stopping, model_checkpoint, reduce_lr]
)

Epoch 1/10


c:\Users\lukas\anaconda3\envs\kia\lib\site-packages\keras\src\trainers\data_adapters\py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()
c:\Users\lukas\anaconda3\envs\kia\lib\site-packages\PIL\Image.py:1000: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(


12/12 ━━━━━━━━━━━━━━━━━━━━ 82s 5s/step - accuracy: 0.3422 - loss: 1.4997 - val_accuracy: 0.3258 - val_loss: 1.1893 - learning_rate: 0.0010
Epoch 2/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 60s 4s/step - accuracy: 0.3986 - loss: 1.1751 - val_accuracy: 0.4045 - val_loss: 1.1911 - learning_rate: 0.0010
Epoch 3/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 59s 4s/step - accuracy: 0.4265 - loss: 1.1501 - val_accuracy: 0.5393 - val_loss: 1.0268 - learning_rate: 0.0010
Epoch 4/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 51s 4s/step - accuracy: 0.5038 - loss: 1.0047 - val_accuracy: 0.6180 - val_loss: 0.9316 - learning_rate: 0.0010
Epoch 5/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 47s 3s/step - accuracy: 0.4520 - loss: 1.0198 - val_accuracy: 0.4831 - val_loss: 0.9292 - learning_rate: 0.0010
Epoch 6/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 45s 3s/step - accuracy: 0.5053 - loss: 0.9459 - val_accuracy: 0.6292 - val_loss: 0.9976 - learning_rate: 0.0010
Epoch 7/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 46s 3s/step - accuracy: 0.5592 - loss: 0.9549 - val_accuracy: 0.5618 - va

In [6]:
base_model.trainable = True
fine_tune_at = 100

# Set the earlier layers to not be trainable
for layer in base_model.layers[:fine_tune_at]:
    layer.trainable = False

# Ensure you include a loss function here
model.compile(optimizer=tf.keras.optimizers.Adam(1e-5), 
              loss='categorical_crossentropy',  # This should be the loss function you used initially
              metrics=['accuracy'])

fine_tune_epochs = 10
total_epochs = history.epoch[-1] + fine_tune_epochs + 1

history_fine = model.fit(
    train_generator,
    epochs=total_epochs,
    initial_epoch=history.epoch[-1],
    validation_data=validation_generator,
    callbacks=[early_stopping, model_checkpoint, reduce_lr]
)


Epoch 10/20
12/12 ━━━━━━━━━━━━━━━━━━━━ 101s 7s/step - accuracy: 0.4401 - loss: 3.5201 - val_accuracy: 0.4607 - val_loss: 0.9513 - learning_rate: 1.0000e-05
Epoch 11/20
12/12 ━━━━━━━━━━━━━━━━━━━━ 78s 6s/step - accuracy: 0.5555 - loss: 2.0987 - val_accuracy: 0.4157 - val_loss: 1.0550 - learning_rate: 1.0000e-05
Epoch 12/20
12/12 ━━━━━━━━━━━━━━━━━━━━ 73s 6s/step - accuracy: 0.4555 - loss: 1.7529 - val_accuracy: 0.4157 - val_loss: 1.2538 - learning_rate: 1.0000e-05
Epoch 13/20
12/12 ━━━━━━━━━━━━━━━━━━━━ 72s 6s/step - accuracy: 0.5554 - loss: 1.0633 - val_accuracy: 0.4157 - val_loss: 1.4237 - learning_rate: 2.0000e-06
Epoch 14/20
12/12 ━━━━━━━━━━━━━━━━━━━━ 75s 6s/step - accuracy: 0.5212 - loss: 1.2389 - val_accuracy: 0.4157 - val_loss: 1.7295 - learning_rate: 2.0000e-06


In [7]:
model.save('pokemon_classifier_model.keras')

